## Part 1: Modular Inverses
### Mathematical Background
Recall that two integers $x,y$ are called relatively prime if the gcd $(x,y) = 1$. In this case, there exist unique integers $a,b$ such that
$$ a\cdot x + b\cdot y = 1. $$
We can use this identity to derive the inverse of $x \mod y$, since clearly
$$1 = a\cdot x + b\cdot y \equiv a\cdot x \mod y,$$
that is, $a\equiv x^{-1}\mod n$.

The way we find such $a,b$ is through the Euclidian algorithm with *back-substitution*. As an exapmle, consider the case where $x = 16$ and $y = 121$. Using the Euclidan algorithm, we compute the following:

1. $121 = 7(16) + 9$
2.  $16 = 1(9) + 7$
3.   $9 = 1(7) + 2$
4.   $7 = 3(2) + 1$

So, $(16, 121) = 1$. In order to find $16^{-1}\mod 121$, we can rearrange the above equations as:
1. $9 = 121 - 7(16)$
2. $7 = 16 - 1(9)$
3. $2 = 9 - 1(7)$
4. $1 = 7 - 3(2)$

And now, by substituting back through our intermediate remainders, we have
$$ 1 = 7 - 3(2) =  7 - 3(9 - (1)7) = (4)7 - (3)9 $$
$$ 1 = 4(16 - 1(9)) - 3(9) = 4(16) - 7(9)$$
$$ 1 = 4(16) - 7(121 - 7(16)) = (53)16 - (7)121 $$
Thus, we found our coefficients:
$$ 1 = (53)16 - (7)121 $$
We can confirm this:

In [1]:
53*16 + (-7)*121 == 1

True

Note that the above method (also known as the *Extended Euclidan Algorithm*) can find the coefficients of any B&eacute;zout identity (i.e., any equation of the form $ax + by = d$, where $d = \mathrm{gcd}(x,y)$) whether or not $x$ and $y$ are relatively prime. In this Investigation Module, you will augment the `gcd` function from I.M. 1 to compute these coefficients using the Extended Euclidian Algorithm.

### Forward Substitution: An Alternative

To make things easier, we will opt for a method of computation which is more "code-friendly" than back-substitution. Take a look again at our re-written expressions for the successive remainders in the above example
1. $9 = 121 - 7(16)$
2. $7 = 16 - 1(9)$
3. $2 = 9 - 1(7)$
4. $1 = 7 - 3(2)$

Note that we could just as well have found our coefficients by substituting our consecutive remainders as we computed them. For example, we can substitute our result for the 9 in the first equation into the second equation to write 7 as a combination of 16 and 121 (our $x$ and $y$), and then use the result for 9 and this new result for 7 to write 2 as a combination of 16 and 121, and then finally using the result for 7 and this new result for 2 to get our desired B&eacute;zout identity. In this way, we can think of the algorithm as starting out with an "approximate" B&eacute;zout identity, and then transorming this identity as it propagates down through the consecutively-decreasing remainders until we arrive at the "exact" B&eacute;zout identity. This is good for us, because it means that we can view the Extended Euclidian Algorithm more as an augmentation to successive steps in the Euclidian Algorithm rather than a separate algorithm attached at the end (back-substitution), which makes it easier to integrate into code we have already written for `gcd`.

Viewing each successive remainder as a combination of 16 and 121 lends itself nicely to a tabular form, which we will call an *EEA table* [Childs]. For the above example, the EEA table would have the form

|          |$q$        |c.121        |c.16        |
:---------:|:---------:|:-----------:|:----------:|
121        | N/A         | 1           | 0          |
16         | 7         | 0           | 1          |
9          | 1         | 1           | -7         |
7          | 1         | -1          | 8          |
2          | 3         | 2           | -15        |
1          | 2         | -7          | 53         |

The columns require some explanation. The entries in the first column (except that in the first row) are numbers which appear as divisors in the Euclidan Algorithm (i.e., those numbers $l_i$ in equations $g_i = q_il_i + r_i$). The numbers in the second column are the the quotients of the divisors in the first column (those numbers $q_i$ in $g_i = q_il_i + r_i$). Note that since 121 never appears as a divisor, it has no quotient, and hence its column entry of N/A. The third and fourth columns indicate how the corresponding entry in the first column can be written as a combination of 16 and 121. For example, $121 = 1\cdot 121 + 0\cdot 16$ (obviously), and $7 = (-1)\cdot 121 + 8\cdot 16$. The B&eacute;zout identity is given by the last row in the table.

At a glance, it is not obvious why we would want to record the quotients of the divisors in the table. The reason is that, in our method of forward substitution, the quotients are needed to construct the next row. For example, assume we know the information encoded in all rows except the last in the above table. This last row corresponds to equation (4) above: $1 = 7 - 3(2)$. If we did not know the quotient corresponding to 2 (which is 3), we would be unable to determine how to write 1 as a combination of 16 and 121, since we would not know by how much we should scale 2's combination.

Let's go through the example of constructing the above table. To begin, we start construction the first two rows of the table, which correspond to 121 and 16.
|   |$q$|c.121|c.16|
|:-:|:-:|:---:|:--:|
|121|N/A|1    |0   |
|16 |?  |0    |1   |

We do not yet know the quotient corresponding to 16 since we have not yet ran the Euclidan Algorithm on 121 and 16, which is our next step. We get $121 = 7\cdot 16 + 9 \Rightarrow 9 = 121 - 7\cdot 16$. We now have enough information to complete the second row and begin construction on the third row
|   |$q$|c.121|c.16|
|:-:|:-:|:---:|:--:|
|121|N/A|1    |0   |
|16 |7  |0    |1   |
|9  |?  |1    |-7  |

We can view the calculation of the coefficient columns of the third row as taking those same columns in the first row and subtracting 7 times those columns in the second row. The quotient of 9 is given by running the Euclidan Algorithm on 16 and 9: $16 = 1\cdot 9 + 7 \Rightarrow 7 = 16 - 1\cdot 9$. This also lets us construct the next row, as before.
|   |$q$|c.121|c.16|
|:-:|:-:|:---:|:--:|
|121|N/A|1    |0   |
|16 |7  |0    |1   |
|9  |1  |1    |-7  |
|7  |?  |-1   |8   |

Again, we can view the calculation of coefficient columns of the fourth row as taking the coefficient columns of the second row and subtracting 1 times those columns in the third row. We continue construction of the table in this fashion until we have hit our gcd:

$9 = 1\cdot 7 + 2 \Rightarrow 2 = 9 - 1\cdot 7$
|   |$q$|c.121|c.16|
|:-:|:-:|:---:|:--:|
|121|N/A|1    |0   |
|16 |7  |0    |1   |
|9  |1  |1    |-7  |
|7  |1  |-1   |8   |
|2  |?  |2    |-15 |

$7 = 2\cdot 3 + 1 \Rightarrow 1 = 7 - 2\cdot 3$
|   |$q$|c.121|c.16|
|:-:|:-:|:---:|:--:|
|121|N/A|1    |0   |
|16 |7  |0    |1   |
|9  |1  |1    |-7  |
|7  |1  |-1   |8   |
|2  |3  |2    |-15 |
|1  |?  |-7   |53  |

We could stop at this point without computing the quotient corresponding to 1 since we are ultimately interested in the coefficients of the last row and nothing else.

You probably noticed that entries in the coefficient columns follow a recurrence. If $C_i$ and $q_i$ are the coefficient in the **c.121** column and the quotient, respectively, the $i^{\mathrm{th}}$ row, then we have
\[
C_i = C_{i-2}-q_{i-1}C_{i-1}
\]
The coefficients $c_i$ in the **c.16** column follow the exact same recurrence
\[
c_i = c_{i-2}-q_{i-1}c_{i-1}
\]
Note that this recurrence comes from our computation for the successive remainders: $r = g - ql$. $C_{i-2}$ and $c_{i-2}$ correspond to the coefficients of 121 and 16 in the combination for $g$, and $C_{i-1}$ and $c_{i-1}$ correspond to the coefficients of 121 and 16 in the combination for $l$.

We now have a forward-iterative means of computing the B&eacute;zout identity for any two integers $x$ and $y$. All we need now is a way of storing successive values in
Sage.

### Sage Interulde: More on Lists

In the first Investigation Module, we introduced a data structure --- a **list** --- as an ordered sequence of objects that can be used as an iterable in `for` loops. The more-typical use case for lists, though, is as an array of storage for data. This data can be anything: numbers, character strings, and even other lists can be stored and accessed in a list. The way we access list elements is through the **index** operator `[]`. For example, if we have the list `p = [2,3,5,7,11]` of the first 5 prime numbers, then `p[2]` gives us back 5. You might expect 5 to be given by `p[3]` and not `p[2]` since it is clearly the third element in the list, but in Sage (and in many other languages), lists are *zero-indexed*, meaning that the first element is actually given by index $0$, and so, inductively, the $N^{th}$ element is given by index $N - 1$. We can also change list elements using regular assignment, so if we do something like `p[4] = 13`, `p` would then look like `[2,3,5,7,13]`.

Another really nice thing about Sage lists is that they can be extended using the built-in `append` function.

In [4]:
p = [2,3,5,7,11]
p.append(13)
p

[2, 3, 5, 7, 11, 13]

`append` takes a single argument and tacks that on to the end of the list calling the function. This function is a little different from the standalone functions we have seen before in that it is called in the context of some *calling object* (in this case, a list) using the dot `.` operator. Without getting too much into the details, this pretty much just makes sure that `append` has something to append to (after all, what would a standalone append function even *do*?).

Let's put lists to use by writing a function that will return a list of the first $n$ Fibonacci numbers. Recall that the Fibonacci sequence is given by the recurrence
$$F_0 = 0, F_1 = 1, F_n = F_{n-1} + F_{n-2}$$
We will start by making a list with the first two Fibonacci numbers `fibs = [0,1]`, and then iteratively adding to this list until we have computed the $n^\mathrm{th}$ term in the sequence.

In [5]:
def fibonacci(n):
    fibs = [0,1]                           #Initial conditions
    for i in range(2,n):                   #Indexing by which fibonacci number we are on currently
        nextfib = fibs[i-1] + fibs[i-2]    #Recurrence
        fibs.append(nextfib)               #Add to the running list

    return (fibs)

fibonacci(10)

[0, 1, 1, 2, 3, 5, 8, 13, 21, 34]

### Exercise 1: Extended Euclidian Algorithm (`eea`)

Write the function `eea`, which takes two integers $x$ and $y$ as input and returns a pair of coefficients satisfying their B&eacute;zout identity (two integers $a$ and $b$ satisfying $ax + by = d$, where $d = \gcd(a,b)$). You can return two numbers at once by putting them in a list and then returning the list. Your implementation may make use of the forward-substitution-based approach discussed above, or some other approach, if you so choose. In either case, we have provided the code implementing the `gcd` function as a starting point; feel free to add, modify, or delete as much code as you need to get your implementation working.

Hint: You will want to avoid saving all of the coefficients, as the storage size tends to grow quickly when dealing with large numbers. Instead save only the coefficients needed for the next step of the algorithm.

In [8]:
def eea(a,b):
    g = max(a,b)
    l = min(a,b)
    q = g // l
    r = g % l
    # Add new stuff here
    while (r != 0):
        g = l
        l = r
        q = g // l
        r = g % l
        # And also here

    return # Return your calculated coefficients as (C, c)

In [9]:
eea(121,16)==[-7,53]

False

# Exercise 2: RSA
Next, you will implement basic RSA encryption and decryption functions.

Recall that in RSA encryption, the receiver privately selects two (large) prime numbers $p$ and $q$. Then, they calculate their modulus $m$ as
$$ m = p\cdot q.$$
They then select some number $e$ which is relatively prime to the Euler phi function of $m$, that is, some $e$ such that
$$ \gcd(e, \varphi(m)) = \gcd(e, (p-1)(q-1)) = 1. $$
The receiver then broadcasts their _public key_ $e$ and their _modulus_ $m$, while keeping their _private key_ $e^{-1} \mod \varphi(m)$.

To send a message, the sender must:
1. Encode their message to integers (in our case we will use ASCII);
2. Break their encoded message $x$ into substrings $x_i$, with each $x_i<m$;
3. For each substring, compute $x_i^e \mod m$;
4. Send each substring.

Upon receiving the message, the receiver must:
1. Decrypt each substring using their private key $e^{-1} \mod \varphi(m)$.
2. Recombine the substrings into the final message.


We have provided some helper functions to break the message up into substrings, as well as placed the calls to those functions in their appropriate places in the `encrypt` and `decrypt` functions.

In [10]:
# Takes an plain-text string `message` as input
# Returns a list of integers 0 <= xi <= 255
# corresponding to the ASCII value of each character
def chunkMessage(message):
    return [ord(char) for char in message]
chunkMessage("Hello!")

[72, 101, 108, 108, 111, 33]

In [11]:
# Takes a list of decoded message fragments `chunks`
# Returns a plain-text string
def recombineMessage(chunks):
    return ''.join(chr(chunk) for chunk in chunks)
recombineMessage([72, 101, 108, 108, 111, 33])

'Hello!'

In [0]:
def encryptRSA(message, publicKey, modulus):
    chunks = chunkMessage(message)
    encryptedChunks = []
    for chunk in chunks:
        # do your encryption here :)
    return encryptedChunks

In [0]:
def decryptRSA(messageChunks, publicKey, p, q):
    decryptedChunks = []
    for chunk in messageChunks:
        # do your decryption here :)
    return recombineMessage(decryptedChunks)

Use the following example values for $p$, $q$, and $e$ to test your encoding and decoding function.

In [0]:
p = 5521
q = 8951
m = p*q
e = 283
secretMessage = [21397500,
                 29648381,
                 22279508,
                 17750870,
                 29115787,
                 31642437,
                 19496101,
                 47295440,
                 48435771,
                 6540145,
                 24554171,
                 39178182,
                 16590202,
                 31642437,
                 17750870,
                 25974362,
                 16462654,
                 17750870,
                 29648381,
                 13930179,
                 19496101,
                 17154213,
                 47295440,
                 13930179,
                 16493895]

decryptRSA(secretMessage, e, p, q)